In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import glob, os, re, string
from datetime import datetime
from nltk.tokenize import sent_tokenize, word_tokenize, RegexpTokenizer
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from nltk.sentiment.vader import SentimentIntensityAnalyzer
from polyglot.detect import Detector
from wordcloud import WordCloud

/opt/conda/lib/python3.6/site-packages/nltk/twitter/__init__.py:20: UserWarning: The twython library has not been installed. Some functionality from the twitter package will not be available.
  warnings.warn("The twython library has not been installed. "


In [3]:
FDIR = 'data/ca_unclean/*/*.csv'

files = [file for file in glob.glob(FDIR)]
files

['data/ca_unclean/cdge/twitter_comfortdelgro.csv',
 'data/ca_unclean/cdge/reddit_comfortdelgro.csv',
 'data/ca_unclean/cdge/twitter_cdgtaxi.csv',
 'data/ca_unclean/cdge/gplay_cdge.csv',
 'data/ca_unclean/cdge/reddit_cdgtaxi.csv',
 'data/ca_unclean/grab/reddit_grab_driver.csv',
 'data/ca_unclean/grab/twitter_grabshare.csv',
 'data/ca_unclean/grab/twitter_GrabSG.csv',
 'data/ca_unclean/grab/twitter_grab_taxi_ride.csv',
 'data/ca_unclean/grab/twitter_grab_driver.csv',
 'data/ca_unclean/grab/gplay_grab_en.csv',
 'data/ca_unclean/grab/twitter_justgrab.csv',
 'data/ca_unclean/grab/twitter_grabtaxi.csv',
 'data/ca_unclean/grab/reddit_grab_taxi_ride.csv',
 'data/ca_unclean/grab/twitter_str_grabcar_en.csv',
 'data/ca_unclean/grab/fb_groups_grab_en.csv',
 'data/ca_unclean/grab/reddit_grabcar.csv',
 'data/ca_unclean/grab/reddit_justgrab.csv',
 'data/ca_unclean/grab/twitter_str_grabhitch_en.csv',
 'data/ca_unclean/grab/reddit_grabtaxi.csv',
 'data/ca_unclean/grab/reddit_GrabSG.csv',
 'data/ca_uncl

In [4]:
prefixes = ['fb', 'twitter', 'gplay', 'reddit']

files_prefixed = [[f for f in files if prefix in f] for prefix in prefixes]

files_prefixed

[['data/ca_unclean/grab/fb_groups_grab_en.csv'],
 ['data/ca_unclean/cdge/twitter_comfortdelgro.csv',
  'data/ca_unclean/cdge/twitter_cdgtaxi.csv',
  'data/ca_unclean/grab/twitter_grabshare.csv',
  'data/ca_unclean/grab/twitter_GrabSG.csv',
  'data/ca_unclean/grab/twitter_grab_taxi_ride.csv',
  'data/ca_unclean/grab/twitter_grab_driver.csv',
  'data/ca_unclean/grab/twitter_justgrab.csv',
  'data/ca_unclean/grab/twitter_grabtaxi.csv',
  'data/ca_unclean/grab/twitter_str_grabcar_en.csv',
  'data/ca_unclean/grab/twitter_str_grabhitch_en.csv',
  'data/ca_unclean/ryde/twitter_ryde.csv',
  'data/ca_unclean/ryde/twitter_rydesg.csv',
  'data/ca_unclean/ryde/twitter_rydepool.csv',
  'data/ca_unclean/tada/twitter_tada_mvl.csv',
  'data/ca_unclean/gojek/twitter_gojek.csv',
  'data/ca_unclean/gojek/twitter_go-jek.csv'],
 ['data/ca_unclean/cdge/gplay_cdge.csv',
  'data/ca_unclean/grab/gplay_grab_en.csv',
  'data/ca_unclean/ryde/gplay_ryde_en.csv',
  'data/ca_unclean/tada/gplay_tada_en.csv'],
 ['data

In [8]:
new_dir = 'data/ca_cleaned/'

if not os.path.exists(new_dir):
    os.makedirs(new_dir)

In [2]:
def add_lang(df, col_name):
    detect_lang = lambda comment: Detector(str(comment), quiet=True).languages[0]

    df['lang_code'] = df.apply(lambda row: detect_lang(row[col_name]).code, axis=1)
    df['lang_sig'] = df.apply(lambda row: detect_lang(row[col_name]).confidence, axis=1)
    
    return df

In [11]:
def process_google_play(f):
    gp_head = ['name', 'date', 'rating', 'comment']
    df = pd.read_csv(f, names=gp_head, encoding='utf-8')
    df['date'] = pd.to_datetime(df['date'])
    
    return add_lang(df, 'comment')

In [69]:
def process_reddit(f):
    df = pd.read_csv(f)
    return add_lang(df, 'title')

In [67]:
def process_twitter(f):
    df = pd.read_csv(f, encoding='iso-8859-1')
    df['tweet'] = df['tweet'].apply(lambda row: ''.join([x for x in row if x in string.printable]))
    return add_lang(df, 'tweet')

In [34]:
for f in files_prefixed[1]:
    print(f.split('/')[-1])

twitter_comfortdelgro.csv
twitter_cdgtaxi.csv
twitter_grabshare.csv
twitter_GrabSG.csv
twitter_grab_taxi_ride.csv
twitter_grab_driver.csv
twitter_justgrab.csv
twitter_grabtaxi.csv
twitter_str_grabcar_en.csv
twitter_str_grabhitch_en.csv
twitter_ryde.csv
twitter_rydesg.csv
twitter_rydepool.csv
twitter_tada_mvl.csv
twitter_gojek.csv
twitter_go-jek.csv


In [46]:
files_prefixed[1][5],files_prefixed[1][10]

('data/ca_unclean/grab/twitter_grab_driver.csv',
 'data/ca_unclean/ryde/twitter_ryde.csv')

In [60]:
df_test = pd.read_csv(files_prefixed[1][5],encoding='iso-8859-1')
df_test['tweet'].astype(str)
df_test.dtypes

id                   object
conversation_id      object
created_at           object
date                 object
time                 object
timezone             object
user_id             float64
username             object
name                 object
place                object
tweet                object
tags                 object
replies              object
mentions             object
urls                 object
photos               object
replies_count       float64
retweets_count      float64
likes_count         float64
location             object
hashtags             object
link                 object
retweet             float64
gif_url              object
gif_thumb            object
video_url            object
video_thumb          object
is_quote_status     float64
quote_id            float64
quote_url            object
is_reply_to         float64
has_parent_tweet    float64
dtype: object

In [65]:
for f in (files_prefixed[1][5], files_prefixed[1][10]):
    df = pd.read_csv(f, encoding='iso-8859-1')
    df['tweet'] = df['tweet'].apply(lambda row: ''.join([x for x in str(row) if x in string.printable]), convert_dtype=str)
    df = add_lang(df, 'tweet')
    
    cur_dir = new_dir + f.split('/')[2] + '/'
    if not os.path.exists(cur_dir):
        os.makedirs(cur_dir)
    
    df[df['lang_code'] == 'en'].to_csv(cur_dir + f.split('/')[-1])

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

...

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

In [76]:
for f in files_prefixed[-1][11:]:
    df = process_reddit(f)
    print(len(df[df['lang_code'] == 'en'].index) / float(len(df.index)))

1.0


In [5]:
for f in files_gp:
    gp_head = ['name', 'date', 'rating', 'comment']
    df = pd.read_csv(f, names=gp_head, encoding='utf-8')
    df['date'] = pd.to_datetime(df['date'])
    
    df = add_lang(df, 'comment')
    
    df[df['lang_code'] == 'en'].to_csv(new_dir + '/' + f[5:], encoding='utf-8')

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

...

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

In [19]:
for f in files_tw:
    df = pd.read_csv(f)
    df = add_lang(df, 'tweet')
    
    df[df['lang_code'] == 'en'].to_csv(new_dir + '/' + f[5:])

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

...

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.


error: ('input contains invalid UTF-8 around byte 44 (of 78)', 'occurred at index 904')

In [28]:
for f in files_fb:
    df = pd.read_csv(f, encoding='utf-8')
    df = add_lang(df, 'comment')
    
    df[df['lang_code'] == 'en'].to_csv(new_dir + '/' + f[5:], encoding='utf-8')

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

...

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

In [29]:
def process_google_play(f):
    gp_head = ['name', 'date', 'rating', 'comment']
    df = pd.read_csv(f, names=gp_head, encoding='utf-8')
    df['date'] = pd.to_datetime(df['date'])
    df['source'] = f[5:]
    
    return add_lang(df, 'comment')

gp_list = [process_google_play(f) for f in files_gp]

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

...

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

AttributeError: 'list' object has no attribute 'concat'

In [30]:
gp_all = pd.concat(gp_list)
gp_all.to_csv(new_dir + '/' + 'gplay_consolidated.csv')
gp_all[gp_all['lang_code'] == 'en'].to_csv(new_dir + '/' + 'gplay_consolidated_en.csv')

In [5]:
def process_twitter(f):
    df = pd.read_csv(f, encoding='iso-8859-1')
    return add_lang(df, 'tweet')

tw_list = [process_twitter(f) for f in files_tw]

error: ('input contains invalid UTF-8 around byte 2 (of 173)', 'occurred at index 3')

In [37]:
tw_all = pd.concat(tw_list)
tw_all.to_csv(new_dir + '/' + 'twitter_consolidated.csv')
tw_all[tw_all['lang_code'] == 'en'].to_csv(new_dir + '/' + 'twitter_consolidated_en.csv')

NameError: name 'tw_list' is not defined

In [3]:
df_re_com = pd.read_csv('data/reddit/comments.csv')
df_re_com

submission_id       id                                               body  \
0          9mumb4  e7hgamb   \r\n\r\nIndonesian ride-hailing firm Go-Jek h...   
1          9mumb4  e7ijo29  If you're one of the people complaining about ...   
2          9mumb4  e7hr49w  Please help take Grab down a peg... they reall...   
3          9mumb4  e7hiiqy                 A new player has entered the game.   
4          9mumb4  e7hxf2y                                Here we go again...   
5          9mumb4  e7i2t9f                just gonna wait for the promo codes   
6          9mumb4  e7hpf08  In the long term, the one who wins is the one ...   
7          9mumb4  e7hgeq6                     Go Jek soon rename Go Jek Cao.   
8          9mumb4  e7i7qy8                  As a passenger, I can't wait!\r\n   
9          9gfm1r  e63t7dl  Singapore is next, as per the article.\r\n\r\n...   
10         9gfm1r  e644q2e                             Come to singapore pls!   
11         9gfm1r  e645zuf  Based on a recent interview with the founder, ...   
12         9gfm1r  e64658b  Has anyone here tried to get a grab in Indones...   
13         9gfm1r  e63wo8z  They are supposed to launch in SG first then V...   
14         9gfm1r  e64gy1n  yup. more competitor, more service and more ch...   
15         9gfm1r  e64fobo  I had a bad experience on uber in 2017. Was go...   
16         9gfm1r  e64gyzl  depends. if you are in Bali, this things can h...   
17         9gfm1r  e64kr2a  I tried last week in Bali! No issues except so...   
18         9gfm1r  e64mnkc  not like that anymore. nowadays a lot of malls...   
19         9gfm1r  e640tux  > With all non-comfort being locked with Grab,...   
20         87s2hh  dwf3sbl  Awesome. Let’s hope they come to Singapore soo...   
21         87s2hh  dwf4npb  Gojek is an unicorn start up and work just nic...   
22         87s2hh  dwg67ud                                          [deleted]   
23         87s2hh  dwf2td8  Given the article said 1 country in the next f...   
24         87s2hh  dwg16w5  excellent news if they come here. We really ne...   
25         87s2hh  dwgujf3  Gojek is phenomenal! From gofood , gosend , go...   
26         87s2hh  dwguyhr                       Here Comes A New Challenger!   
27         87s2hh  dwgwcnc  Am i missing something here.... has gojek expa...   
28         87s2hh  dwgx7qd                                         Go-food!!!   
29         87s2hh  dwg5j9f  So interesting\r\n\r\nSBS vs SMRT \r\n\r\nGrab...   
..            ...      ...                                                ...   
279        9u3b7o  e919v49  Is it just me or is this not really funny, at ...   
280        9u3b7o  e91gm59  People are lazy lol. When I worked pt for mcd ...   
281        9u3b7o  e91erhr                            ya sia! mktg oversight!   
282        9u3b7o  e91lr3h  Yes, they've announced their intention to ente...   
283        9u3b7o  e91frij  Also better ask them don't pre-slice, otherwis...   
284        9u3b7o  e91f2yw                      Back to the pizza restaurant    
285        9u3b7o  e927iyz                 Wah then order fried rice how????    
286        9u3b7o  e9174kk                                     One single fry   
287        9u3b7o  e92ldvo                                           just you   
288        9u3b7o  e91j2yv  No la maybe first timer user grabfood promo th...   
289        9u3b7o  e91sqeo  And that is how you get obesity, diabetes and ...   
290        9u3b7o  e9218pl                                           RYDE too   
291        9u3b7o  e91epx0                                           mic drop   
292        9u3b7o  e919gw1                        One single popcorn chicken.   
293        9u3b7o  e91nled                         OP said Mcdelivery though.   
294        9u3b7o  e91blb6                                        One nugget    
295        9u3b7o  e91bm3o             Actually no, one single kernel of corn   
296        8xr04q  e252chk         

In [4]:
before = len(df_re_com.index)
df_re_com = add_lang(df_re_com, 'body')
df_re_com

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

submission_id       id                                               body  \
0          9mumb4  e7hgamb   \r\n\r\nIndonesian ride-hailing firm Go-Jek h...   
1          9mumb4  e7ijo29  If you're one of the people complaining about ...   
2          9mumb4  e7hr49w  Please help take Grab down a peg... they reall...   
3          9mumb4  e7hiiqy                 A new player has entered the game.   
4          9mumb4  e7hxf2y                                Here we go again...   
5          9mumb4  e7i2t9f                just gonna wait for the promo codes   
6          9mumb4  e7hpf08  In the long term, the one who wins is the one ...   
7          9mumb4  e7hgeq6                     Go Jek soon rename Go Jek Cao.   
8          9mumb4  e7i7qy8                  As a passenger, I can't wait!\r\n   
9          9gfm1r  e63t7dl  Singapore is next, as per the article.\r\n\r\n...   
10         9gfm1r  e644q2e                             Come to singapore pls!   
11         9gfm1r  e645zuf  Based on a recent interview with the founder, ...   
12         9gfm1r  e64658b  Has anyone here tried to get a grab in Indones...   
13         9gfm1r  e63wo8z  They are supposed to launch in SG first then V...   
14         9gfm1r  e64gy1n  yup. more competitor, more service and more ch...   
15         9gfm1r  e64fobo  I had a bad experience on uber in 2017. Was go...   
16         9gfm1r  e64gyzl  depends. if you are in Bali, this things can h...   
17         9gfm1r  e64kr2a  I tried last week in Bali! No issues except so...   
18         9gfm1r  e64mnkc  not like that anymore. nowadays a lot of malls...   
19         9gfm1r  e640tux  > With all non-comfort being locked with Grab,...   
20         87s2hh  dwf3sbl  Awesome. Let’s hope they come to Singapore soo...   
21         87s2hh  dwf4npb  Gojek is an unicorn start up and work just nic...   
22         87s2hh  dwg67ud                                          [deleted]   
23         87s2hh  dwf2td8  Given the article said 1 country in the next f...   
24         87s2hh  dwg16w5  excellent news if they come here. We really ne...   
25         87s2hh  dwgujf3  Gojek is phenomenal! From gofood , gosend , go...   
26         87s2hh  dwguyhr                       Here Comes A New Challenger!   
27         87s2hh  dwgwcnc  Am i missing something here.... has gojek expa...   
28         87s2hh  dwgx7qd                                         Go-food!!!   
29         87s2hh  dwg5j9f  So interesting\r\n\r\nSBS vs SMRT \r\n\r\nGrab...   
..            ...      ...                                                ...   
279        9u3b7o  e919v49  Is it just me or is this not really funny, at ...   
280        9u3b7o  e91gm59  People are lazy lol. When I worked pt for mcd ...   
281        9u3b7o  e91erhr                            ya sia! mktg oversight!   
282        9u3b7o  e91lr3h  Yes, they've announced their intention to ente...   
283        9u3b7o  e91frij  Also better ask them don't pre-slice, otherwis...   
284        9u3b7o  e91f2yw                      Back to the pizza restaurant    
285        9u3b7o  e927iyz                 Wah then order fried rice how????    
286        9u3b7o  e9174kk                                     One single fry   
287        9u3b7o  e92ldvo                                           just you   
288        9u3b7o  e91j2yv  No la maybe first timer user grabfood promo th...   
289        9u3b7o  e91sqeo  And that is how you get obesity, diabetes and ...   
290        9u3b7o  e9218pl                                           RYDE too   
291        9u3b7o  e91epx0                                           mic drop   
292        9u3b7o  e919gw1                        One single popcorn chicken.   
293        9u3b7o  e91nled                         OP said Mcdelivery though.   
294        9u3b7o  e91blb6                                        One nugget    
295        9u3b7o  e91bm3o             Actually no, one single kernel of corn   
296        8xr04q  e252chk         

In [6]:
len(df_re_com.index)/before

1.0

In [8]:
df_re_topics = pd.read_csv('data/reddit/merged.csv')
df_re_topics

title  score      id  \
0            Go-Jek revs up to get going in Singapore     24  9mumb4   
1   Indonesia's Go-Jek could 'soon' launch its rid...     17  9gfm1r   
2   Go-Jek to expand to 4 Southeast Asian countrie...     39  87s2hh   
3   Grab looks to avoid a price war with ride-hail...     24  9s9yjs   
4   Go-Jek Singapore Is Now Hiring: Interested Dri...     47  9s9w2g   
5   Singapore's competition watchdog to consider G...     42  8ly3j2   
6       Unhappy Grab drivers hope for Go-Jek lifeline     16  9sjvyj   
7           Go-Jek plans to enter S’pore in Oct. 2018      4  9l8xui   
8   [Premium]South-east Asian rivals Go-Jek and Gr...     95  88vjmd   
9   Grab to pay $6.42m anti-competition fine as it...     55  9qbrmt   
10  Go-Jek in head-to-head fight with Grab for S-E...     31  9o8c3f   
11  In aggressive expansion, Go-Jek to enter Singa...     99  8lpg4r   
12  Go-Jek's Singapore debut may fall short of Gra...     10  9nj1gm   
13                   Understanding the rise of Go-Jek     12  8gin51   
14  Go-Jek could launch ride-hailing service in Si...    111  9l08uq   
15  Saw an article on Go Jek. Asking why not use m...      4  8mn33h   
16  Go-Jek is in talks with former Uber ally Comfo...     35  8eimi4   
17                            Last 12 hours with Uber     78  8hkvz9   
18  [Premium]Not everything is up for Grab in Sout...     18  8av0kh   
19  [Premium]Grab signs up 'thousands' of Uber dri...      9  89yuog   
20                          why delivery took so long    890  9u3b7o   
21  Grab unveils open platform strategy to build S...      8  8xr04q   

                                                  url  comms_num  \
0   https://www.straitstimes.com/singapore/transpo...          9   
1   https://www.cnbc.com/2018/09/14/indonesias-go-...         11   
2   https://www.reddit.com/r/singapore/comments/87...         27   
3   https://www.scmp.com/tech/enterprises/article/...         11   
4   https://vulcanpost.com/650291/go-jek-singapore...          7   
5   https://www.reddit.com/r/singapore/comments/8l...         18   
6   https://www.straitstimes.com/singapore/transpo...         19   
7   https://mothership.sg/2018/10/go-jek-october-s...          0   
8   http://www.straitstimes.com/singapore/transpor...         19   
9   https://www.straitstimes.com/singapore/transpo...          8   
10  https://www.businesstimes.com.sg/startups/go-j...          8   
11  https://www.reddit.com/r/singapore/comments/8l...         34   
12  https://sbr.com.sg/transport-logistics/in-focu...          5   
13  https://www.todayonline.com/commentary/lessons...          2   
14  https://www.scmp.com/tech/enterprises/article/...         27   
15  https://www.reddit.com/r/singapore/comments/8m...         22   
16  https://techcrunch.com/2018/04/23/go-jek-is-in...          8   
17                https://i.redd.it/48m8gxyy1dw01.jpg         16   
18  http://www.straitstimes.com/asia/se-asia/not-e...          5   
19  http://www.straitstimes.com/singapore/transpor...          3   
20                https://i.redd.it/sac0qww1ebw11.jpg         32   
21  https://www.grab.com/sg/press/business/grab-un...         12   

         created                                               body  \
0   1.539160e+09                                                NaN   
1   1.537172e+09                                                NaN   
2   1.522274e+09  Having used their services several times befor...   
3   1.540815e+09                                                NaN   
4   1.540815e+09                                                NaN   
5   1.527242e+09   *SINGAPORE — Indonesian ride\-hailing giant G...   
6   1.540895e+09                                                NaN   
7   1.538658e+09                                                NaN   
8   1.522659e+09                                                NaN   
9   1.540225e+09                                                NaN   
10  1.539596e+09                             

In [9]:
before = len(df_re_topics.index)
df_re_topics = add_lang(df_re_topics, 'title')
df_re_topics

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.


title  score      id  \
0            Go-Jek revs up to get going in Singapore     24  9mumb4   
1   Indonesia's Go-Jek could 'soon' launch its rid...     17  9gfm1r   
2   Go-Jek to expand to 4 Southeast Asian countrie...     39  87s2hh   
3   Grab looks to avoid a price war with ride-hail...     24  9s9yjs   
4   Go-Jek Singapore Is Now Hiring: Interested Dri...     47  9s9w2g   
5   Singapore's competition watchdog to consider G...     42  8ly3j2   
6       Unhappy Grab drivers hope for Go-Jek lifeline     16  9sjvyj   
7           Go-Jek plans to enter S’pore in Oct. 2018      4  9l8xui   
8   [Premium]South-east Asian rivals Go-Jek and Gr...     95  88vjmd   
9   Grab to pay $6.42m anti-competition fine as it...     55  9qbrmt   
10  Go-Jek in head-to-head fight with Grab for S-E...     31  9o8c3f   
11  In aggressive expansion, Go-Jek to enter Singa...     99  8lpg4r   
12  Go-Jek's Singapore debut may fall short of Gra...     10  9nj1gm   
13                   Understanding the rise of Go-Jek     12  8gin51   
14  Go-Jek could launch ride-hailing service in Si...    111  9l08uq   
15  Saw an article on Go Jek. Asking why not use m...      4  8mn33h   
16  Go-Jek is in talks with former Uber ally Comfo...     35  8eimi4   
17                            Last 12 hours with Uber     78  8hkvz9   
18  [Premium]Not everything is up for Grab in Sout...     18  8av0kh   
19  [Premium]Grab signs up 'thousands' of Uber dri...      9  89yuog   
20                          why delivery took so long    890  9u3b7o   
21  Grab unveils open platform strategy to build S...      8  8xr04q   

                                                  url  comms_num  \
0   https://www.straitstimes.com/singapore/transpo...          9   
1   https://www.cnbc.com/2018/09/14/indonesias-go-...         11   
2   https://www.reddit.com/r/singapore/comments/87...         27   
3   https://www.scmp.com/tech/enterprises/article/...         11   
4   https://vulcanpost.com/650291/go-jek-singapore...          7   
5   https://www.reddit.com/r/singapore/comments/8l...         18   
6   https://www.straitstimes.com/singapore/transpo...         19   
7   https://mothership.sg/2018/10/go-jek-october-s...          0   
8   http://www.straitstimes.com/singapore/transpor...         19   
9   https://www.straitstimes.com/singapore/transpo...          8   
10  https://www.businesstimes.com.sg/startups/go-j...          8   
11  https://www.reddit.com/r/singapore/comments/8l...         34   
12  https://sbr.com.sg/transport-logistics/in-focu...          5   
13  https://www.todayonline.com/commentary/lessons...          2   
14  https://www.scmp.com/tech/enterprises/article/...         27   
15  https://www.reddit.com/r/singapore/comments/8m...         22   
16  https://techcrunch.com/2018/04/23/go-jek-is-in...          8   
17                https://i.redd.it/48m8gxyy1dw01.jpg         16   
18  http://www.straitstimes.com/asia/se-asia/not-e...          5   
19  http://www.straitstimes.com/singapore/transpor...          3   
20                https://i.redd.it/sac0qww1ebw11.jpg         32   
21  https://www.grab.com/sg/press/business/grab-un...         12   

         created                                               body  \
0   1.539160e+09                                                NaN   
1   1.537172e+09                                                NaN   
2   1.522274e+09  Having used their services several times befor...   
3   1.540815e+09                                                NaN   
4   1.540815e+09                                                NaN   
5   1.527242e+09   *SINGAPORE — Indonesian ride\-hailing giant G...   
6   1.540895e+09                                                NaN   
7   1.538658e+09                                                NaN   
8   1.522659e+09                                                NaN   
9   1.540225e+09                                                NaN   
10  1.539596e+09                             

In [10]:
len(df_re_topics.index)/before

1.0